## Language Identification & Gender Identification

* Imports

In [36]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sb
from sklearn.metrics import accuracy_score,confusion_matrix,classification_report
from sklearn.model_selection import cross_val_score,train_test_split
from sklearn.pipeline import Pipeline
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.tokenize import sent_tokenize

%matplotlib inline

#### Question 1:
* Language Identification

First we need to import all the langauge texts.
For the corpus we used the corpus from: http://wortschatz.uni-leipzig.de/en/download/
all corpus are contain 10k sentences

In [37]:
with open('english.txt',encoding='utf-8') as f:
    english = f.read()

    
english_df = pd.DataFrame(english.lower().splitlines())
english_df.head()
en_string = 'english'
english_df['Language'] = en_string
print('\n')
print(english_df.head())

with open('dutch.txt',encoding='utf-8') as f:
    dutch = f.read()

    
dutch_df = pd.DataFrame(dutch.lower().splitlines())
dutch_df.head()
du_string = 'dutch'
dutch_df['Language'] = du_string
print('\n')
print(dutch_df.head())

with open('spanish.txt',encoding='utf-8') as f:
    spanish = f.read()

    
spanish_df = pd.DataFrame(spanish.lower().splitlines())
spanish_df.head()
sp_string = 'spanish'
spanish_df['Language'] = sp_string
print('\n')
print(spanish_df.head())

with open('italian.txt',encoding='utf-8') as f:
    italian = f.read()

    
italian_df = pd.DataFrame(italian.lower().splitlines())
italian_df.head()
it_string = 'italian'
italian_df['Language'] = it_string
print('\n')
print(italian_df.head())

with open('german.txt',encoding='utf-8') as f:
    german = f.read()

    
german_df = pd.DataFrame(german.lower().splitlines())
german_df.head()
ge_string = 'german'
german_df['Language'] = ge_string
print('\n')
print(german_df.head())



                                                   0 Language
0             1\tintrigued i started to work it out.  english
1  2\tthe third installment of "the twilight saga...  english
2  3\tlowrie atoned for an error he made in the t...  english
3  4\tbut she couldn’t sleep, knowing that her mo...  english
4  5\tbridge: call the minot ywca at 838-1812 to ...  english


                                                   0 Language
0                1\tjuist om die ruimte te scheppen.    dutch
1  2\top deze site vindt u meer informatie over o...    dutch
2  3\tin zeeland kan de formatie van naaldwijk di...    dutch
3               4\top zoek naar een unieke beleving?    dutch
4  5\tsinds 1984 heeft hij een breed scala aan ke...    dutch


                                                   0 Language
0  1\tprobablemente las lluvias de diciembre y co...  spanish
1  2\tcuenta con áreas de hidroterapia, terapias ...  spanish
2  3\tdoctoras, enfermeras, bailarinas!; cantante...  spanish
3 

In [38]:
#After we've imported all of our texts and split them into sentences
#lets combine them into one DataFrame
english_df = english_df.append(italian_df)
english_df = english_df.append(spanish_df)
english_df = english_df.append(dutch_df)
english_df = english_df.append(german_df)
Languages = english_df
Languages.shape

(50011, 2)

In [5]:
#Lets add an index so we can map our languages
Languages['Language Index'] = Languages['Language']
mapping = {'english':0,'spanish':1,'italian':2,'dutch':3,'german':4}
Languages = Languages.replace({'Language Index':mapping})

In [7]:
#Now to make it fair, we need to shuffle our DataFrame
from sklearn.utils import shuffle
Languages = shuffle(Languages)
Languages.head()

0 Language  \
2790  2790\tsì, gli ultimissimi provvedimenti per co...  italian   
7504            7505\tsin embargo el sicario midió mal.  spanish   
2656  2655\twenn sie auf den artikel »45-millionen-e...   german   
524   525\tstichting ander geld adviseert mine over ...    dutch   
6952  6950\tso können sie gewinnen: folgen sie diese...   german   

      Language Index  
2790               2  
7504               1  
2656               4  
524                3  
6952               4

In [8]:
#Lets change our column's names for better work
Languages.columns = [['Sentence','True Label','Language Index']]
Languages.head()

Sentence True Label  \
2790  2790\tsì, gli ultimissimi provvedimenti per co...    italian   
7504            7505\tsin embargo el sicario midió mal.    spanish   
2656  2655\twenn sie auf den artikel »45-millionen-e...     german   
524   525\tstichting ander geld adviseert mine over ...      dutch   
6952  6950\tso können sie gewinnen: folgen sie diese...     german   

     Language Index  
2790              2  
7504              1  
2656              4  
524               3  
6952              4

In [9]:
#Split our Features and labels for assessment
Language_features = Languages['Sentence'].values
Language_label = Languages['Language Index'].values

In [10]:
#Splitting our data to train and test
xtrain,xtest,ytrain,ytest = train_test_split(Language_features,Language_label,
                                             test_size=0.2,random_state=42)

In [14]:
#Use TfidfVectorizer to vectorize our sentences and splitting it to 4-grams
#While using Multinomial Naive Bayes to classify it
from sklearn.naive_bayes import MultinomialNB
tfidf_vect = TfidfVectorizer(analyzer='char',ngram_range=(3,5))
model = MultinomialNB()
text_clf = Pipeline([('tfidf', tfidf_vect),('clf', model), ])

In [15]:
#Since our train is an array of sentences, and an array has no lower function
# We use ravel to alter our xtrain   
text_clf.fit(xtrain.ravel(), ytrain)

C:\Users\Gilad\Anaconda3\lib\site-packages\sklearn\utils\validation.py:578: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


Pipeline(memory=None,
     steps=[('tfidf', TfidfVectorizer(analyzer='char', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=1.0, max_features=None, min_df=1,
        ngram_range=(3, 5), norm='l2', preprocessor=None, smooth_idf=True,
 ...rue,
        vocabulary=None)), ('clf', MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True))])

In [17]:
#Check our precision
predictions = text_clf.predict(xtest.ravel())
print(classification_report(ytest,predictions,target_names=mapping))

             precision    recall  f1-score   support

    english       1.00      1.00      1.00      2018
    spanish       1.00      1.00      1.00      1996
    italian       1.00      1.00      1.00      1956
      dutch       1.00      1.00      1.00      2007
     german       1.00      1.00      1.00      2026

avg / total       1.00      1.00      1.00     10003



In [21]:
print("Accuracy Score: {}".format(accuracy_score(ytest,predictions)))
scores = cross_val_score(text_clf,Language_features.ravel(),Language_label.ravel(),cv=5)
print("\n\nMean cross-validation accuracy: " + str(scores.mean()))

Accuracy Score: 0.9988003598920324


Mean cross-validation accuracy: 0.9991202139198304


In [147]:
def assignLanguage(Language):
    
    true_values = np.array(ytest)
    
    for i,sentence in enumerate(xtest):
        prediction = float(predictions[i])
        true_value = float(ytest[i])
        print('Predicted Language Index: {}'.format(prediction))
        print('Actural Language Index: {}'.format(true_value))
        print("Sentence:\n {}".format(sentence))
        print('\n')

In [148]:
assignLanguage(Languages)

Predicted Language Index: 2.0
Actural Language Index: 2.0
Sentence:
 ['7176\til film "enter the void", del regista francese gaspard noã©, ha ottenuto il narciso del miglior lungometraggio al festival internazionale del film fantastico di neuchã¢tel (nifff) che si ã¨ concluso questa sera.']


Predicted Language Index: 4.0
Actural Language Index: 4.0
Sentence:
 ['8974\thier riecht es nach nichts - offenbar ein gutes zeichen.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['662\tshares rose as much as 7% before retreating a bit.']


Predicted Language Index: 4.0
Actural Language Index: 4.0
Sentence:
 ['9684\tim vergleich zum vorjahresabschnitt entspricht dies einem anstieg um 131 prozent.']


Predicted Language Index: 1.0
Actural Language Index: 1.0
Sentence:
 ['3625\targenpress.info - prensa argentina para todo el mundo: estudian en la provincia argentina de córdoba la incidencia de cáncer de colon entre hombres y mujeres (titel).']


Predicted Language Index: 2

 ['9557\tla mattina alle 6, con le prime luci del giorno, puoi vederne decine e decine per le strade.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['809\tslate makes no comments on zuckerberg’s hair, but does agree that old people make better entrepreneurs.']


Predicted Language Index: 2.0
Actural Language Index: 2.0
Sentence:
 ['6522\tlo ha fatto l\'arcivescovo di canterbury, rowan williams, leader spirituale della chiesa d\'inghilterra, che ha accusato la chiesa cattolica in irlanda di aver "perso tutta la sua credibilita il tutto a sei mesi dalla visita di benedetto xvi a londra.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ["7290\ti was waiting around the whole day and going on court, you know, after like i don't know how many hours of sitting around, and then you don't finish the match."]


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['4860\tand, as for the future?']


Predicted Language Index: 1.0
A

Actural Language Index: 4.0
Sentence:
 ['9945\tsein vorgänger viktor juschtschenko hatte dies strikt abgelehnt.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['9701\t\x93when adults cannot tell the difference between these lighters and toys, how can we expect a young child to do so?\x94 mr. coan said.']


Predicted Language Index: 3.0
Actural Language Index: 3.0
Sentence:
 ['1657\tvoorop blijft staan dat we ernaar streven de kwaliteit van onze dienstverlening op peil te houden.']


Predicted Language Index: 2.0
Actural Language Index: 2.0
Sentence:
 ['3813\tdenis ha fatto bene, si smarca e sono molto contento di come sta giocando.']


Predicted Language Index: 1.0
Actural Language Index: 1.0
Sentence:
 ['103\ty el ahora célebre "chi-chi-chi, le-le-le, viva chile" me despertó una tarde de domingo a través de la ventana.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['8219\tin the meantime, hollerado will have to spend their time tour

Predicted Language Index: 4.0
Actural Language Index: 4.0
Sentence:
 ['571\tberlin (az) - bundesarbeitsministerin ursula von der leyen (cdu), will in der kommenden woche ihr konzept für die neuorganisation der jobcenter vorlegen.']


Predicted Language Index: 1.0
Actural Language Index: 1.0
Sentence:
 ['8728\t"superiores a las cuantías de 2010".']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['287\tan earthquake measuring magnitude 4.0 struck yogyakarta and surrounding cities at 8:30 a.m. thursday, according to the antara state news agency.']


Predicted Language Index: 1.0
Actural Language Index: 1.0
Sentence:
 ['6033\tlos veteranos senadores demócratas russ feingold, de wisconsin, y blanche lincoln, de arkansas, perdieron en sus intentos de salir reelegidos.']


Predicted Language Index: 3.0
Actural Language Index: 3.0
Sentence:
 ['3244\tde vrijheid van godsdienst is natuurlijk een groot goed, betogen zij om beurten, maar nieuw onderzoek van de universiteit 

Predicted Language Index: 3.0
Actural Language Index: 3.0
Sentence:
 ["9197\thet spreekuur is elke derde maandag van de maand 's avonds van zeven tot acht in huize scherpenzeel."]


Predicted Language Index: 1.0
Actural Language Index: 1.0
Sentence:
 ['5304\tla mayoría de las universidades catalanas prefieren guardar silencio hasta que se apruebe la iniciativa.']


Predicted Language Index: 3.0
Actural Language Index: 3.0
Sentence:
 ['7181\tdie doelen zijn niet gehaald.']


Predicted Language Index: 3.0
Actural Language Index: 3.0
Sentence:
 ['4475\tde ziekte van lyme wordt gekenmerkt door het opkomen van een rode verkleuring op de huid bij de beet van de teek (het zogeheten erythema migrans).']


Predicted Language Index: 4.0
Actural Language Index: 4.0
Sentence:
 ['1079\tdas ist das ergebnis einer aktuellen berechnung der abda - bundesvereinigung deutscher apothekerverbände.']


Predicted Language Index: 3.0
Actural Language Index: 3.0
Sentence:
 ['5436\took volwassenen kunnen bij ju

...

 ['6478\twhile the protests might be over, no one can guarantee our safety in cyber space.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['6723\tits early, but thats the way you look at it.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['9191\tjunior brendan robertson was runnerup clocking 16:55 to lead westborough and teammate zach polich was fourth with a time of 17:07.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['974\tthe father, a veteran, smoothed the america flag along the length of the casket, and the sobbing family huddled to be closest to the son and brother they lost.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['6707\tthe leading scorer for bessemer citys girls team could miss the rest of the season with a knee injury.']


Predicted Language Index: 1.0
Actural Language Index: 1.0
Sentence:
 ['8127\thay algunas pequeñas tiendas de abarrotes que venden sodas y fritu

Sentence:
 ['9369\tdijo que el mismo presidente chávez se declaró marxista el 15 de enero pasado en esta asamblea y «está decidido a convertir a venezuela en un estado socialista.']


Predicted Language Index: 1.0
Actural Language Index: 1.0
Sentence:
 ['5048\tla primera, que se deriva de una crisis de la economía real, y no al revés.']


Predicted Language Index: 1.0
Actural Language Index: 1.0
Sentence:
 ['1619\tel año pasado clausuraron cinco lugares donde realizaban estas fiestas y detuvieron a los propietarios de las viviendas.']


Predicted Language Index: 3.0
Actural Language Index: 3.0
Sentence:
 ['2063\tmet vijf waren ze om al na vijf kilometer weg te rijden: juan antonio flecha, chris horner, carlos da cruz, thomas voeckler en ludovic turpin.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['6266\ton the other, they will all suffer, and will all have to pay the price of increased safety and maintenance regulations in the gulf.']


Predicted Language I

Actural Language Index: 4.0
Sentence:
 ['7595\tso ist es gute christliche tradition.']


Predicted Language Index: 3.0
Actural Language Index: 3.0
Sentence:
 ['1479\teen mogelijke locatie voor een gebouwde parkeervoorziening is het van beuningenplein.']


Predicted Language Index: 1.0
Actural Language Index: 1.0
Sentence:
 ['8195\tdespués, y como era de esperar, con una espectacular actuación ante los medios de comunicación de todo el mundo destacados en cannes, donde las carcajadas han vuelto a brotar a cada ocurrencia del genio.']


Predicted Language Index: 4.0
Actural Language Index: 4.0
Sentence:
 ['6327\tunter anderem wird der bolzplatz mit einem asphaltbelag versehen.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['7741\tshe used the phrase, healthy people, healthy family, health food and healthy checkbook.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['9480\tat the plate, jerome pena finished the night with three hits and t

Actural Language Index: 1.0
Sentence:
 ['3968\tluego, los cineastas justin schein y laura ga-bbert reprodujeron lo que vivió esta familia en el documental no impact man, que integra la programación del green film fest y que es otra de las películas más destacadas de la programación.']


Predicted Language Index: 4.0
Actural Language Index: 4.0
Sentence:
 ['4366\tin 2012 werde die gesellschaft einen umsatzschub durch das neue joint venture mit man im bereich der landfahrzeuge erfahren.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['9327\tjay clemons can be found on twitter, day and night (@si_jayclemons), accessing your fantasy questions and comments.']


Predicted Language Index: 2.0
Actural Language Index: 2.0
Sentence:
 ['9680\tl&rsquo;aumento medio per i 118 mila medici e veterinari pubblici è di circa 179 euro lordi mensili.']


Predicted Language Index: 4.0
Actural Language Index: 4.0
Sentence:
 ['2423\tin deutschland gibt es noch einige freiwillige anp

Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ['1296\tthe pounding hooves of the cavalry can be heard in the distance, however, as the opposition is hoping to step in and save the arts in the military.']


Predicted Language Index: 4.0
Actural Language Index: 4.0
Sentence:
 ['6517\tsie kommen aus ländern zwischen dem balkan und dem himalaja.']


Predicted Language Index: 1.0
Actural Language Index: 1.0
Sentence:
 ['9111\tno se detuvo un minuto a meditarlo.']


Predicted Language Index: 2.0
Actural Language Index: 2.0
Sentence:
 ['4545\tpossono uccidere come in irak e in nord italia senza che i militari criminali siano puniti.']


Predicted Language Index: 1.0
Actural Language Index: 1.0
Sentence:
 ['4027\ta los 14 años fue la primera vez que conocí la cárcel y ha habido una continuidad ahí, y cada día que pasa uno pues sencillamente se va comprometiendo más.']


Predicted Language Index: 0.0
Actural Language Index: 0.0
Sentence:
 ["32\tpresident ahmadinejad furth

#### Question 2:
* Gender Identification

In [39]:
#First lets read our dataset
text =pd.read_excel('NickNames.xlsx',sep='\t')
text.isna().sum()
text[text.Gender.isna()==True]

Nick Gender
23444  nameriascreations    NaN
23488         namefabric    NaN
26649        namejingyun    NaN

In [41]:
#we can see that there are a few NaN's let check how many are there
text.isna().sum()

Nick      0
Gender    3
dtype: int64

In [42]:
#Not so many so lets drop them
text = text.dropna()

In [43]:
#Lets map our genders to 0 and 1's so we can use some classification methods 
text.Gender = text.Gender.replace({"female":0,"male":1})
text.head()

Nick  Gender
0     shelbeemcbride       0
1       tainapudalov       0
2        mattpresley       1
3              katec       0
4  hazlewwoodheather       0

In [124]:
#convert name to a feature vector 
def convert_name(name):
    arr = np.zeros(26*26+5)
    name = str(name)
    for x in range(len(name)-1):
        ind = (ord(name[x])-ord('b'))*26 + (ord(name[x+1])-ord('b'))
        arr[ind] += 1
    return arr

In [125]:
name_map = np.vectorize(convert_name, otypes=[np.ndarray])
Xlist = name_map(text['Nick'])
Gender_features = np.array(Xlist.tolist())
Gender_labels = text['Gender']

In [126]:
from sklearn.ensemble import RandomForestClassifier
for x in range(1):
    xtrain_gender, xtest_gender, ytrain_gender, ytest_gender = train_test_split(Gender_features,Gender_labels, test_size=0.2,random_state=42)
    clf = RandomForestClassifier(n_estimators=10)
    clf.fit(xtrain_gender, ytrain_gender)

In [127]:
predictions_gender = clf.predict(xtest_gender)
print(classification_report(ytest_gender,predictions_gender,target_names={"female":0,"male":1}))

print("Accuracy Score: {}".format(accuracy_score(ytest_gender,predictions_gender)))
scores = cross_val_score(clf,Gender_features,Gender_labels,cv=5)
print("\n\nMean cross-validation accuracy: " + str(scores.mean()))

             precision    recall  f1-score   support

     female       0.79      0.95      0.86      5303
       male       0.75      0.36      0.49      2120

avg / total       0.78      0.78      0.76      7423

Accuracy Score: 0.7828371278458844


Mean cross-validation accuracy: 0.7825172571155663


In [128]:
from sklearn.linear_model import LogisticRegression
for x in range(1):
    log_reg = LogisticRegression()
    log_reg.fit(xtrain_gender, ytrain_gender)

In [129]:
predictions_gender = log_reg.predict(xtest_gender)
print(classification_report(ytest_gender,predictions_gender,target_names={"female":0,"male":1}))

print("Accuracy Score: {}".format(accuracy_score(ytest_gender,predictions_gender)))
scores = cross_val_score(log_reg,Gender_features,Gender_labels,cv=5)
print("\n\nMean cross-validation accuracy: " + str(scores.mean()))

             precision    recall  f1-score   support

     female       0.81      0.91      0.86      5303
       male       0.69      0.47      0.56      2120

avg / total       0.78      0.79      0.77      7423

Accuracy Score: 0.7883605011450896


Mean cross-validation accuracy: 0.7877447770341572


In [143]:
def assignGender(text):
    Names = text['Nick']
    Labels = Gender_labels
    gender_predict = clf.predict(Gender_features)
    for name,Label,Predict in zip(Names,Labels, gender_predict):
        print("\nName: {}".format(name))
        print("True Gender:{}".format(Label))
        print("Predicted Gender: {}".format(Predict))

In [144]:
assignGender(text)


Name: shelbeemcbride
True Gender:0
Predicted Gender: 0

Name: tainapudalov
True Gender:0
Predicted Gender: 0

Name: mattpresley
True Gender:1
Predicted Gender: 1

Name: katec
True Gender:0
Predicted Gender: 0

Name: hazlewwoodheather
True Gender:0
Predicted Gender: 0

Name: melodypelham
True Gender:0
Predicted Gender: 0

Name: mirandaandras
True Gender:0
Predicted Gender: 0

Name: melodygbrunet
True Gender:0
Predicted Gender: 0

Name: zariahlanae
True Gender:0
Predicted Gender: 0

Name: taiyac
True Gender:0
Predicted Gender: 0

Name: hoyteshakira
True Gender:1
Predicted Gender: 0

Name: efrainmendoza
True Gender:1
Predicted Gender: 1

Name: shakiyajones
True Gender:0
Predicted Gender: 0

Name: gwenreese
True Gender:0
Predicted Gender: 1

Name: alayahsaunders
True Gender:0
Predicted Gender: 0

Name: hadarshka
True Gender:0
Predicted Gender: 0

Name: mahoganyjoachim
True Gender:0
Predicted Gender: 0

Name: kaitlanjex
True Gender:0
Predicted Gender: 0

Name: queenmorales
True Gender:0
Pr

Predicted Gender: 0

Name: breonnacole
True Gender:0
Predicted Gender: 0

Name: retagorges
True Gender:0
Predicted Gender: 0

Name: johanaq
True Gender:0
Predicted Gender: 0

Name: carogabbidon
True Gender:0
Predicted Gender: 0

Name: moneydontmakeme
True Gender:0
Predicted Gender: 0

Name: laracballard
True Gender:0
Predicted Gender: 0

Name: hilasepo
True Gender:0
Predicted Gender: 0

Name: mayoral
True Gender:1
Predicted Gender: 0

Name: tanikquaparker
True Gender:0
Predicted Gender: 0

Name: livilexwell
True Gender:0
Predicted Gender: 0

Name: miahammfan
True Gender:0
Predicted Gender: 0

Name: rehananeville
True Gender:0
Predicted Gender: 0

Name: emilshitrit
True Gender:1
Predicted Gender: 1

Name: julietatolm
True Gender:0
Predicted Gender: 0

Name: andreinadican
True Gender:0
Predicted Gender: 0

Name: miriasraf
True Gender:0
Predicted Gender: 0

Name: dangerajia
True Gender:1
Predicted Gender: 1

Name: tomasaharak
True Gender:0
Predicted Gender: 0

Name: joslynnlopez
True Gend

Name: ornagur
True Gender:0
Predicted Gender: 0

Name: minahbabyyy
True Gender:0
Predicted Gender: 0

Name: kristajean
True Gender:0
Predicted Gender: 0

Name: katoriap
True Gender:1
Predicted Gender: 1

Name: williamsnyisha
True Gender:1
Predicted Gender: 0

Name: jeannettegonzalez
True Gender:0
Predicted Gender: 0

Name: shelilosh
True Gender:0
Predicted Gender: 0

Name: meccamayeux
True Gender:0
Predicted Gender: 0

Name: kasharawashington
True Gender:0
Predicted Gender: 0

Name: miroxrmz
True Gender:1
Predicted Gender: 1

Name: aranne
True Gender:1
Predicted Gender: 1

Name: nathalieotero
True Gender:0
Predicted Gender: 0

Name: modestoportillo
True Gender:1
Predicted Gender: 1

Name: nelsonlarry
True Gender:1
Predicted Gender: 1

Name: alexissurrett
True Gender:0
Predicted Gender: 0

Name: pinklaydeez
True Gender:1
Predicted Gender: 1

Name: whitemartin
True Gender:1
Predicted Gender: 1

Name: malenaeckenrod
True Gender:0
Predicted Gender: 0

Name: kirkdm
True Gender:1
Predicted G

Name: daizya
True Gender:0
Predicted Gender: 0

Name: jemarocampo
True Gender:1
Predicted Gender: 1

Name: chelseyjones
True Gender:0
Predicted Gender: 0

Name: devereauxfam
True Gender:1
Predicted Gender: 1

Name: maddiecrismanmc
True Gender:0
Predicted Gender: 0

Name: mirelaw
True Gender:0
Predicted Gender: 0

Name: fernandez
True Gender:0
Predicted Gender: 0

Name: giovannaagonzalez
True Gender:0
Predicted Gender: 0

Name: dulcetg
True Gender:0
Predicted Gender: 0

Name: tarastarr
True Gender:1
Predicted Gender: 0

Name: jayanaraison
True Gender:0
Predicted Gender: 0

Name: montygirl
True Gender:1
Predicted Gender: 1

Name: amorris
True Gender:0
Predicted Gender: 0

Name: genaufo
True Gender:0
Predicted Gender: 0

Name: shainalofton
True Gender:0
Predicted Gender: 0

Name: mariaisabelchiu
True Gender:0
Predicted Gender: 0

Name: zariahwhite
True Gender:0
Predicted Gender: 0

Name: liahamblen
True Gender:0
Predicted Gender: 0

Name: garciaemmanuel
True Gender:0
Predicted Gender: 0



Name: beckyyoung
True Gender:0
Predicted Gender: 0

Name: laneshafurlow
True Gender:0
Predicted Gender: 0

Name: liligreen
True Gender:0
Predicted Gender: 0

Name: tritialuk
True Gender:0
Predicted Gender: 0

Name: maleahb
True Gender:0
Predicted Gender: 0

Name: beckys
True Gender:0
Predicted Gender: 0

Name: netamordechay
True Gender:0
Predicted Gender: 0

Name: shameikabaxter
True Gender:0
Predicted Gender: 0

Name: jenningssk
True Gender:1
Predicted Gender: 1

Name: keirahjade
True Gender:0
Predicted Gender: 0

Name: nitagibby
True Gender:0
Predicted Gender: 0

Name: boydtyla
True Gender:1
Predicted Gender: 0

Name: jasiafelders
True Gender:0
Predicted Gender: 0

Name: kalaborders
True Gender:1
Predicted Gender: 1

Name: brianneridge
True Gender:0
Predicted Gender: 0

Name: daveymatey
True Gender:1
Predicted Gender: 1

Name: daishacooper
True Gender:0
Predicted Gender: 0

Name: kristiannakelly
True Gender:0
Predicted Gender: 0

Name: talabr
True Gender:0
Predicted Gender: 0

Name: 

...

True Gender:0
Predicted Gender: 0

Name: fabianachapellin
True Gender:0
Predicted Gender: 0

Name: dalianac
True Gender:0
Predicted Gender: 0

Name: kendrahbranee
True Gender:0
Predicted Gender: 0

Name: salenamcrae
True Gender:0
Predicted Gender: 0

Name: harelyasmin
True Gender:1
Predicted Gender: 1

Name: lironma
True Gender:0
Predicted Gender: 0

Name: penguin
True Gender:1
Predicted Gender: 0

Name: theath
True Gender:0
Predicted Gender: 0

Name: dashanaportovich
True Gender:1
Predicted Gender: 1

Name: makenzischaefer
True Gender:0
Predicted Gender: 0

Name: hadardar
True Gender:0
Predicted Gender: 0

Name: caleighamelio
True Gender:0
Predicted Gender: 0

Name: ellebert
True Gender:0
Predicted Gender: 0

Name: angiegrass
True Gender:0
Predicted Gender: 0

Name: alfordann
True Gender:1
Predicted Gender: 1

Name: natalysal
True Gender:0
Predicted Gender: 0

Name: ashleyannbrush
True Gender:0
Predicted Gender: 0

Name: priceda
True Gender:1
Predicted Gender: 0

Name: kristacottingim

Predicted Gender: 0

Name: lilachtzab
True Gender:0
Predicted Gender: 0

Name: priyanicole
True Gender:0
Predicted Gender: 0

Name: rachealritter
True Gender:0
Predicted Gender: 0

Name: michaelefrenvargas
True Gender:0
Predicted Gender: 0

Name: maegenodenweller
True Gender:0
Predicted Gender: 0

Name: hibabitar
True Gender:0
Predicted Gender: 0

Name: sabrenasimons
True Gender:0
Predicted Gender: 0

Name: lawtonjamilia
True Gender:1
Predicted Gender: 1

Name: yardenshalom
True Gender:1
Predicted Gender: 1

Name: lyndaborel
True Gender:0
Predicted Gender: 0

Name: krystleneeb
True Gender:0
Predicted Gender: 0

Name: galitby
True Gender:0
Predicted Gender: 0

Name: diyaghanta
True Gender:0
Predicted Gender: 0

Name: antoinettenelson
True Gender:0
Predicted Gender: 0

Name: kristiehicks
True Gender:0
Predicted Gender: 0

Name: beckymontoya
True Gender:0
Predicted Gender: 0

Name: mccallc
True Gender:0
Predicted Gender: 0

Name: hobsondennis
True Gender:1
Predicted Gender: 1

Name: chaya

True Gender:1
Predicted Gender: 0

Name: emmaleighv
True Gender:0
Predicted Gender: 0

Name: chellelandry
True Gender:0
Predicted Gender: 0

Name: natalymendoza
True Gender:0
Predicted Gender: 0

Name: kierathomas
True Gender:0
Predicted Gender: 0

Name: addisynaguilar
True Gender:0
Predicted Gender: 0

Name: lesleyanndries
True Gender:0
Predicted Gender: 0

Name: estellaadeestellaade
True Gender:0
Predicted Gender: 0

Name: deshaylahchism
True Gender:0
Predicted Gender: 0

Name: alexustate
True Gender:0
Predicted Gender: 0

Name: mahatia
True Gender:0
Predicted Gender: 0

Name: saritm
True Gender:0
Predicted Gender: 0

Name: koralrubin
True Gender:0
Predicted Gender: 0

Name: marybethchung
True Gender:0
Predicted Gender: 0

Name: jaimeek
True Gender:0
Predicted Gender: 0

Name: wadejessica
True Gender:1
Predicted Gender: 1

Name: mirihb
True Gender:0
Predicted Gender: 0

Name: tarahx
True Gender:0
Predicted Gender: 0

Name: taviat
True Gender:0
Predicted Gender: 0

Name: triaswilliam


Predicted Gender: 0

Name: breeneshaunn
True Gender:0
Predicted Gender: 0

Name: araceliesteban
True Gender:0
Predicted Gender: 0

Name: latiawilliam
True Gender:0
Predicted Gender: 0

Name: starrant
True Gender:0
Predicted Gender: 1

Name: brayanpro
True Gender:1
Predicted Gender: 1

Name: karthikeyanmaheswaran
True Gender:1
Predicted Gender: 0

Name: yaseenbrown
True Gender:1
Predicted Gender: 0

Name: marinaovilfeldman
True Gender:0
Predicted Gender: 0

Name: shakeriahenry
True Gender:0
Predicted Gender: 0

Name: keannelizabeth
True Gender:1
Predicted Gender: 1

Name: yalondah
True Gender:0
Predicted Gender: 0

Name: keshatondo
True Gender:0
Predicted Gender: 0

Name: nikeyalewis
True Gender:0
Predicted Gender: 0

Name: natoriabrooks
True Gender:0
Predicted Gender: 0

Name: sherylwalford
True Gender:0
Predicted Gender: 0

Name: detraceasar
True Gender:0
Predicted Gender: 0

Name: catinalopez
True Gender:0
Predicted Gender: 0

Name: murraygenine
True Gender:1
Predicted Gender: 1

Nam

True Gender:0
Predicted Gender: 0

Name: brinamcarthur
True Gender:0
Predicted Gender: 0

Name: jadorexjasmine
True Gender:0
Predicted Gender: 0

Name: jenezamc
True Gender:0
Predicted Gender: 0

Name: portlandnash
True Gender:0
Predicted Gender: 0

Name: gregoriosharpe
True Gender:1
Predicted Gender: 1

Name: lolax
True Gender:0
Predicted Gender: 0

Name: daved
True Gender:1
Predicted Gender: 1

Name: jannymann
True Gender:0
Predicted Gender: 0

Name: hillybilly
True Gender:1
Predicted Gender: 1

Name: williamsshantrell
True Gender:1
Predicted Gender: 1

Name: brownronnya
True Gender:1
Predicted Gender: 1

Name: marinagolan
True Gender:0
Predicted Gender: 0

Name: ngocle
True Gender:0
Predicted Gender: 0

Name: kennedialexis
True Gender:0
Predicted Gender: 0

Name: chasitypryor
True Gender:0
Predicted Gender: 0

Name: rudolfreyeslao
True Gender:1
Predicted Gender: 1

Name: abbygailalmanza
True Gender:0
Predicted Gender: 0

Name: pinkneyp
True Gender:1
Predicted Gender: 1

Name: nicola